In [1]:
import os
import matplotlib.pyplot as plt
from scipy import stats
import pyspark.sql.functions as F
import pyspark.sql.types as T

os.getcwd()
os.chdir("/mnt/workspace/Public-DSC291/notebooks/Section2-PCA/Full_Dataset_analysis")
os.getcwd()

from Startup import *

finished standard imports
dict_items([('spark.executor.memory', '3g'), ('spark.cores.max', '4'), ('spark.app.name', 'Weather_PCA'), ('spark.executor.cores', '1'), ('spark.default.parallelism', '10'), ('spark.logConf', 'True')])
started SparkContext and SQLContext in 13.57 seconds
loaded weather.parquet in 8.40 seconds
loaded stations.parquet in 0.20 seconds
registered dataframes as tables in 0.22 seconds


In [2]:
import urllib
import folium
import branca
import json
import requests
import ssl
import math
ssl._create_default_https_context = ssl._create_unverified_context

url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data'
state_geo = url + '/us-states.json'
county_geo = url + '/us_counties_20m_topo.json'
county_data = url + '/us_county_data.csv'

temp_df = pd.read_csv(url + '/US_Unemployment_Oct2012.csv')
US_states = list(temp_df['State'])
ElNinoYears = [1951, 1957, 1965, 1968, 1972, 1977, 1982, 1991, 1997]
FIPS_set = list(pd.read_csv(county_data, na_values=[' '])['FIPS_Code'])[1:]

save_path = '/mnt/workspace/Public-DSC291/hw3/results/'

def getFIPS(lat, lon):
    url = urllib.request.urlopen("https://geo.fcc.gov/api/census/area?lat=" 
                                 + str(lat) + "&lon=" + str(lon) + "&format=json")
    data = json.loads(url.read().decode())
    FIPS = data['results'][0]['county_fips']
    return int(FIPS)

In [3]:
%%time
query="""
SELECT stations.ID, weather.Year, stations.state, stations.latitude, stations.longitude, weather.Values
FROM stations
LEFT JOIN weather
ON stations.ID = weather.Station
WHERE stations.state <> '' AND weather.Measurement='SNOW'
"""

print(query)
Weather_df=sqlContext.sql(query)
sqlContext.registerDataFrameAsTable(Weather_df,'Weather_df')


SELECT stations.ID, weather.Year, stations.state, stations.latitude, stations.longitude, weather.Values
FROM stations
LEFT JOIN weather
ON stations.ID = weather.Station
WHERE stations.state <> '' AND weather.Measurement='SNOW'

CPU times: user 4 ms, sys: 0 ns, total: 4 ms
Wall time: 104 ms


In [4]:
#Filter for certain dates
filter_year = 1945
Weather_df = Weather_df.filter(Weather_df.Year > filter_year)

#Filter for only stations with data in the full range
cnt_bystation = Weather_df.groupBy('ID').count()
Weather_df = Weather_df.join(cnt_bystation, "ID")
mx = cnt_bystation.agg({"count": "max"}).collect()[0]["max(count)"]
Weather_df = Weather_df.filter(Weather_df['count'] == mx)
Weather_pdf = Weather_df.toPandas()

In [5]:
Weather_df.groupby('Year').count().show()

+----+-----+
|Year|count|
+----+-----+
|1959| 1041|
|1990| 1041|
|1975| 1041|
|1977| 1041|
|2003| 1041|
|2007| 1041|
|1974| 1041|
|1955| 1041|
|2006| 1041|
|1978| 1041|
|1961| 1041|
|2013| 1041|
|1952| 1041|
|1956| 1041|
|1988| 1041|
|1997| 1041|
|1994| 1041|
|1968| 1041|
|1951| 1041|
|1973| 1041|
+----+-----+
only showing top 20 rows



In [6]:
def f1(row):
    return row['Values'][:362]

def f2(row):
    return row['Values'][362:]

def Jan2Jun(df):
    df_first = df.copy()
    
    # df_first is same as df except for its ['Values'] column only contains the 
    # the first half year data.
    df_first['V_first'] = df_first.apply(f1, axis=1)
    
    # subtract df_first 'Year' column by 1, because we want to join originally 1998 Jan-Jun to 1997 July-Dec,
    # as 1997 data, so minus 1998 by 1 to match 1997.
    df_first['Year'] = df_first.apply(lambda x: x['Year']-1, axis=1)
    
    # df_second is same as df except for its ['Values'] column only contains the 
    # the second half year data.
    df_second = df.copy()
    df_second['V_second'] = df_second.apply(f2, axis=1)
    
    # drop the inrrelevant columns of df_second so that join can be easier later. I only kept 'ID' and 'Year'
    # that are used to be joined on later.
    df_second = df_second.drop(['state', 'Values', 'latitude',
                                'longitude', 'count'], axis=1)
    
    # join df_first and df_second on ID, Year.
    result = pd.merge(df_first, df_second, on=['ID', 'Year'], how='inner')
    
    # generate the thansformed data, e.g. 1997 July - 1998 June from 'V_second' (1997 July - 1997 Dec) and 
    # 'V_first' (1998 Jan - 1998 June)
    result['Values'] = result.apply(lambda x: x['V_second'] + x['V_first'], axis=1)
    
    # drop V_second and V_first as they are useless now.
    return result.drop(['V_second', 'V_first'], axis=1)

In [7]:
Weather_pdf = Jan2Jun(Weather_pdf)
del Weather_pdf['count']
Values = [np.nansum(unpackArray(v,np.float16)) for v in list(Weather_pdf['Values'])]
Weather_pdf['Values'] = Values
pick = [Weather_pdf['state'][i] in US_states for i in Weather_pdf.index]
Weather_pdf = Weather_pdf[pick]
Weather_pdf = Weather_pdf[Weather_pdf['state'] != 'AK']
Weather_pdf = Weather_pdf[Weather_pdf['state'] != 'HI']
Weather_pdf.sample(5)

ID  Year state  latitude  longitude  Values
22446  USC00250130  1947    NE   42.1103  -102.8967   702.0
21968  USC00418433  2005    TX   32.7100  -100.9111     0.0
34381  USC00449186  1956    VA   39.1833   -78.1167   333.0
66970  USC00118684  1983    IL   39.7950   -88.2900   596.0
27260  USC00344019  2004    OK   36.5381   -98.2661   295.0

In [8]:
import pickle
f = open("/mnt/workspace/Public-DSC291/hw3/FIPS_Code.pkl","rb")
FIPS_dict = pickle.load(f)
f.close()

    
"""
FIPS_dict = dict()
for lat, lon in set(zip(list(Weather_pdf['latitude']), list(Weather_pdf['longitude']))):
    FIPS_dict[(lat, lon)] = getFIPS(lat, lon)
    
# Save
f = open("/mnt/workspace/Public-DSC291/hw3/FIPS_Code.pkl","wb")
pickle.dump(FIPS_dict,f)
f.close()

"""

'\nFIPS_dict = dict()\nfor lat, lon in set(zip(list(Weather_pdf[\'latitude\']), list(Weather_pdf[\'longitude\']))):\n    FIPS_dict[(lat, lon)] = getFIPS(lat, lon)\n    \n# Save\nf = open("/mnt/workspace/Public-DSC291/hw3/FIPS_Code.pkl","wb")\npickle.dump(FIPS_dict,f)\nf.close()\n\n'

In [10]:
FIPS = []
for i in Weather_pdf.index:
    lat = Weather_pdf['latitude'][i]
    lon = Weather_pdf['longitude'][i]
    if (lat, lon) in FIPS_dict:
        FIPS.append(FIPS_dict[(lat, lon)])
    else:
        FIPS.append(getFIPS(lat, lon))

Weather_pdf['FIPS'] = FIPS
Weather_pdf = Weather_pdf[['Year', 'state', 'FIPS', 'Values']]
Weather_pdf = Weather_pdf.drop(Weather_pdf[Weather_pdf['Values']==np.inf].index)
Weather_pdf.sample(5)

Year state   FIPS  Values
2319   1987    NY  36111  2088.0
22090  1993    NE  31103   957.0
45436  1956    KS  20051   506.0
15827  1961    ID  16085  4724.0
62243  1946    UT  49039  1207.0

## State-level Maps

In [11]:
data = []
for s in set(Weather_pdf['state']):
    temp_df = Weather_pdf[Weather_pdf['state']==s]
    for y in set(temp_df['Year']):
        v = np.nanmean(temp_df[temp_df['Year']==y]['Values'])
        data.append([s, y, v])
state_df = pd.DataFrame(data, columns=['state', 'Year', 'Values'])

data = []
for s in set(Weather_pdf['state']):
    temp_df = state_df[state_df['state']==s]
    pick_EN = np.array([temp_df['Year'][i] in ElNinoYears for i in temp_df.index])
    Values_EN = list(temp_df[pick_EN]['Values'])
    Values_NEN = list(temp_df[~pick_EN]['Values'])
    T, P = stats.ttest_ind(Values_EN, Values_NEN)
    Values_DIFF = np.nanmean(Values_EN) - np.nanmean(Values_NEN)
    data.append([s, T, P, Values_DIFF])
state_df = pd.DataFrame(data, columns=['state', 'T', 'P', 'D'])
state_df['logP'] = np.log10(state_df['P'])
state_df.head()

state         T         P           D      logP
0    ME  1.625266  0.108945  309.467433 -0.962791
1    IA  0.607703  0.545502   55.774178 -0.263204
2    AR  0.551199  0.583387   17.426139 -0.234043
3    SD  0.095659  0.924086   10.642481 -0.034288
4    NM  1.186415  0.239777   91.076427 -0.620192

In [23]:
#bins = list(df_1997['avg(Anom_sum)'].quantile([0, 0.2, 0.4, 0.6, 0.8, 1]))
#bins = [-1000, -500, 0, 500, 1000, 2000, 2600]
caption = 'State-level Snowfall Anomalies in El Nino Years'
m = folium.Map(location=[35, -102], zoom_start=4)

folium.Choropleth(
    geo_data=state_geo,
    name='choropleth',
    data=state_df,
    columns=['state', 'D'],
    key_on='feature.id',
    fill_color='RdYlBu',
    fill_opacity=0.7,
    line_opacity=0.2,
    #bins=bins,
    legend_name=caption
).add_to(m)

folium.LayerControl().add_to(m)

m.save(save_path + caption + '.html')
m

In [24]:
#bins = list(df_1997['avg(Anom_sum)'].quantile([0, 0.2, 0.4, 0.6, 0.8, 1]))
#bins = [-1000, -500, 0, 500, 1000, 2000, 2600]
caption = 'State-level Snowfall T-Statistics'
m = folium.Map(location=[35, -102], zoom_start=4)

folium.Choropleth(
    geo_data=state_geo,
    name='choropleth',
    data=state_df,
    columns=['state', 'T'],
    key_on='feature.id',
    fill_color='RdYlBu',
    fill_opacity=0.7,
    line_opacity=0.2,
    #bins=bins,
    legend_name=caption
).add_to(m)

folium.LayerControl().add_to(m)

m.save(save_path + caption + '.html')
m

In [29]:
#bins = list(state_df['P'].quantile([0, 0.001, 0.01, 0.05, 0.8, 1]))
bins = [-3, -2, np.log10(0.05), 0]
caption = 'State-level Snowfall logP-Values'
m = folium.Map(location=[35, -102], zoom_start=4)


folium.Choropleth(
    geo_data=state_geo,
    name='choropleth',
    data=state_df,
    columns=['state', 'logP'],
    key_on='feature.id',
    fill_color='RdYlBu',
    fill_opacity=0.7,
    line_opacity=0.2,
    bins=bins,
    legend_name=caption
).add_to(m)

folium.LayerControl().add_to(m)

m.save(save_path + caption + '.html')
m

## Region-level Maps

In [30]:
data = []
for f in set(Weather_pdf['FIPS']):
    temp_df = Weather_pdf[Weather_pdf['FIPS']==f]
    for y in set(temp_df['Year']):
        v = np.nanmean(temp_df[temp_df['Year']==y]['Values'])
        data.append([f, y, v])
region_df = pd.DataFrame(data, columns=['FIPS', 'Year', 'Values'])

data = []
for f in set(Weather_pdf['FIPS']):
    temp_df = region_df[region_df['FIPS']==f]
    pick_EN = np.array([temp_df['Year'][i] in ElNinoYears for i in temp_df.index])
    Values_EN = list(temp_df[pick_EN]['Values'])
    Values_NEN = list(temp_df[~pick_EN]['Values'])
    T, P = stats.ttest_ind(Values_EN, Values_NEN)
    Values_DIFF = np.nanmean(Values_EN) - np.nanmean(Values_NEN)
    data.append([f, T, P, Values_DIFF])
region_df = pd.DataFrame(data, columns=['FIPS', 'T', 'P', 'D'])
region_df['logP'] = np.log10(region_df['P'])
region_df.head()

FIPS         T         P          D      logP
0  47115  0.730233  0.467872  60.047893 -0.329873
1  45079  0.961490  0.339869  20.557471 -0.468689
2  47131 -0.267784  0.789713 -23.178161 -0.102531
3  47145 -0.024561  0.980480  -1.348659 -0.008561
4  41003 -0.185595  0.853340 -44.574713 -0.068878

In [31]:
region_df.index = range(len(region_df))
temp_df = region_df[region_df['FIPS'] == min(region_df['FIPS'])]

T = [temp_df.iloc[0]['T']]
P = [temp_df.iloc[0]['P']]
D = [temp_df.iloc[0]['D']]
logP = [temp_df.iloc[0]['logP']]

for fips in FIPS_set:
    if fips in list(region_df['FIPS']):
        temp_df = region_df[region_df['FIPS'] == fips]
        T.append(temp_df.iloc[0]['T'])
        P.append(temp_df.iloc[0]['P'])
        D.append(temp_df.iloc[0]['D'])
        logP.append(temp_df.iloc[0]['logP'])
    else:
        T.append(T[-1])
        P.append(P[-1])
        D.append(D[-1])
        logP.append(logP[-1])

T = pd.Series(T[1:], index=list(FIPS_set)).sort_index()
P = pd.Series(P[1:], index=list(FIPS_set)).sort_index()
D = pd.Series(D[1:], index=list(FIPS_set)).sort_index()
logP = pd.Series(logP[1:], index=list(FIPS_set)).sort_index()

In [32]:
def RegionMapPlot(series, colormap):
    
    def style_function(feature):
        value = series.get(int(feature['id'][-5:]), None)
        color = '#ffffff'
        if value:
            color = colormap(value)
        return {
            'fillOpacity': 1,
            'weight': 0,
            'fillColor': color
        }

    m = folium.Map(
        location=[35, -102],
        tiles='cartodbpositron',
        zoom_start=4,
    )

    folium.TopoJson(
        json.loads(requests.get(county_geo).text),
        'objects.us_counties_20m',
        style_function=style_function
    ).add_to(m)

    m.add_child(colormap)
    m.save(save_path + colormap.caption + '.html')

    return m

In [38]:
start = math.floor(min(D))
end = math.ceil(max(D))
colormap = branca.colormap.linear.RdBu_09.scale(start, end) 
#colormap = colormap.to_step(index=[-3, -2, -1, 0, 1, 2, 3, end])
colormap.caption = 'Region-level Snowfall Anomalies in El Nino Years'


RegionMapPlot(D, colormap)

In [34]:
start = math.floor(min(T))
end = math.ceil(max(T))
colormap = branca.colormap.linear.RdBu_09.scale(start, 5) 
#colormap = colormap.to_step(index=[-3, -2, -1, 0, 1, 2, 3, end])
colormap.caption = 'Region-level Snowfall T-Statistics'


RegionMapPlot(T, colormap)

In [40]:
start = math.floor(min(logP))
end = math.ceil(max(logP))
colormap = branca.colormap.linear.RdBu_09.scale(-4, end) 
colormap = colormap.to_step(index=[-4, -3, -2, np.log10(0.05), 0])
colormap.caption = 'Region-level Snowfall loP-Values'

RegionMapPlot(logP, colormap)